In [1]:
#pip install 'transformers[torch]'
import pandas as pd
from transformers import AutoTokenizer, AutoModel
from sklearn.metrics.pairwise import cosine_similarity
import torch
import numpy as np
import matplotlib.pyplot as plt
from sklearn.decomposition import PCA
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics import f1_score
from sklearn.metrics import multilabel_confusion_matrix
from sklearn.metrics import classification_report
import random
import re
from collections import Counter
from random import randint
torch.cuda.is_available()

True

In [2]:
#loading prediction file
path = "/home/kaushal.maurya/selectllm/code/classifer_policy_code/notebook/"

#GSM8K
# filename="gsm8k_predictions.csv" 

#MMLU
filename="mmlu_predictions.csv" 

#Other
# filename="mmlu_results.csv"

#Data Name
data_name = filename.strip().split('_')[0]

data_all= pd.read_csv(path+filename, encoding="utf-8")
data = data_all.loc[data_all['split'] == 'test']
print(data_all.shape, data.shape, data_name)

data_all.head()

(15857, 15) (1530, 15) mmlu


question split           subject  \
0  Find all c in Z_3 such that Z_3[x]/(x^2 + c) i...   val  abstract_algebra   
1  Statement 1 | If aH is an element of a factor ...   val  abstract_algebra   
2  Statement 1 | Every element of a group generat...   val  abstract_algebra   
3  Statement 1| Every function from a finite set ...   val  abstract_algebra   
4  Find the characteristic of the ring 2Z. (A) 0 ...   val  abstract_algebra   

                                          true_label  \
0  ['maj_gemma-7b_LM', 'maj_llama2-7b-lm_LM', 'ma...   
1  ['maj_gemma-7b_LM', 'maj_llama2-7b-lm_LM', 'ma...   
2  ['maj_gemma-7b_LM', 'maj_llama2-7b-lm_LM', 'ma...   
3  ['maj_gemma-7b-it_CHAT', 'maj_gemma-7b_LM', 'm...   
4  ['maj_gemma-7b-it_CHAT', 'maj_gemma-7b_LM', 'm...   

                                    prediction  raw_predictions  \
0  ['maj_gemma-7b_LM', 'maj_mistral-7b-lm_LM']  [0 1 0 0 0 0 1]   
1  ['maj_gemma-7b_LM', 'maj_mistral-7b-lm_LM']  [0 1 0 0 0 0 1]   
2  ['maj_gemma-7b_LM', 'maj_mistral-7b-lm_LM']  [0 1 0 0 0 0 1]   
3  ['maj_gemma-7b_LM', 'maj_mistral-7b-lm_LM']  [0 1 0 0 0 0 1]   
4  ['maj_gemma-7b_LM', 'maj_mistral-7b-lm_LM']  [0 1 0 0 0 0 1]   

                                          confidence gold_answer  \
0  [-0.2244373   0.20402932 -0.20554718 -0.368481...           B   
1  [-0.3301706   0.12753275 -0.19526619 -0.427830...           B   
2  [-0.24231102  0.12812217 -0.17033087 -0.418076...           C   
3  [-0.2288533   0.10934026 -0.16025472 -0.383569...           A   
4  [-0.09687452  0.39072466 -0.15363683 -0.351608...           A   

                        auto_answers_maj_gemma-7b_LM  \
0  ['B', 'B', 'B', 'B', 'B', 'B', 'B', 'B', 'B', ...   
1  ['B', 'B', 'B', 'B', 'B', 'B', 'B', 'B', 'B', ...   
2  ['C', 'C', 'C', 'C', 'C', 'C', 'C', 'C', 'C', ...   
3  ['A', 'A', 'A', 'A', 'A', 'A', 'A', 'A', 'A', ...   
4  ['A', 'A', 'A', 'A', 'A', 'A', 'A', 'A', 'A', ...   

                     auto_answers_maj_metamath-7b_LM  \
0  ['B', 'B', 'B', 'B', 'B', 'B', 'B', 'B', 'B', ...   
1  ['B', 'B', 'B', 'INVALID', 'B', 'B', 'B', 'B',...   
2  ['B', 'B', 'B', 'C', 'D', 'INVALID', 'B', 'B',...   
3  ['A', 'A', 'A', 'A', 'A', 'A', 'A', 'A', 'A', ...   
4  ['A', 'INVALID', 'INVALID', 'INVALID', 'A', 'I...   

                   auto_answers_maj_mistral-7b-lm_LM  \
0  ['B', 'B', 'B', 'B', 'B', 'B', 'B', 'B', 'B', ...   
1  ['B', 'B', 'B', 'B', 'B', 'B', 'B', 'B', 'B', ...   
2  ['C', 'C', 'C', 'C', 'C', 'C', 'C', 'C', 'C', ...   
3  ['A', 'A', 'A', 'A', 'A', 'A', 'A', 'A', 'A', ...   
4  ['A', 'A', 'A', 'A', 'A', 'A', 'A', 'A', 'A', ...   

                    auto_answers_maj_llama2-7b-lm_LM  \
0  ['B', 'B', 'B', 'B', 'B', 'B', 'B', 'B', 'B', ...   
1  ['B', 'A', 'B', 'B', 'B', 'B', 'A', 'B', 'B', ...   
2  ['C', 'C', 'C', 'C', 'C', 'C', 'C', 'C', 'C', ...   
3  ['A', 'A', 'A', 'A', 'A', 'A', 'A', 'A', 'A', ...   
4  ['A', 'A', 'A', 'A', 'A', 'A', 'A', 'A', 'A', ...   

                   auto_answers_maj_gemma-7b-it_CHAT  \
0  ['A', 'A', 'A', 'A', 'A', 'B', 'A', 'C', 'A', ...   
1  ['A', 'A', 'A', 'A', 'A', 'A', 'A', 'A', 'A', ...   
2  ['A', 'A', 'A', 'A', 'A', 'A', 'A', 'A', 'A', ...   
3  ['A', 'A', 'A', 'A', 'A', 'A', 'A', 'A', 'A', ...   
4  ['A', 'A', 'A', 'B', 'C', 'C', 'A', 'B', 'A', ...   

               auto_answers_maj_llama2-13b-chat_CHAT  \
0  ['D', 'D', 'A', 'INVALID', 'D', 'D', 'A', 'D',...   
1  ['A', 'C', 'C', 'A', 'D', 'D', 'D', 'D', 'A', ...   
2  ['C', 'D', 'A', 'A', 'A', 'A', 'B', 'C', 'A', ...   
3  ['C', 'A', 'A', 'C', 'C', 'A', 'C', 'C', 'C', ...   
4  ['A', 'D', 'B', 'B', 'C', 'D', 'C', 'A', 'B', ...   

               auto_answers_maj_mistral-7b-inst_CHAT  
0  ['A', 'INVALID', 'B', 'C', 'A', 'B', 'D', 'B',...  
1  ['D', 'A', 'A', 'A', 'A', 'A', 'A', 'A', 'A', ...  
2  ['C', 'A', 'D', 'C', 'A', 'B', 'A', 'B', 'C', ...  
3  ['C', 'INVALID', 'A', 'D', 'B', 'A', 'A', 'A',...  
4  ['A', 'A', 'A', 'A', 'A', 'A', 'INVALID', 'A',...

In [3]:
data_ = data.copy(deep=True)
data_test = data[["question",	"true_label", 	"prediction"]]
print(data_test.shape)
data_test.head()

(1530, 3)


question  \
14327  The cyclic subgroup of Z_24 generated by 18 ha...   
14328  Find the order of the factor group Z_6/<3>. (A...   
14329  Statement 1 | A permutation that is a product ...   
14330  Find the order of the factor group (Z_4 x Z_12...   
14331  Find the maximum possible order for some eleme...   

                                              true_label  \
14327  ['maj_gemma-7b-it_CHAT', 'maj_gemma-7b_LM', 'm...   
14328     ['maj_gemma-7b-it_CHAT', 'maj_metamath-7b_LM']   
14329  ['maj_gemma-7b-it_CHAT', 'maj_gemma-7b_LM', 'm...   
14330                           ['maj_mistral-7b-lm_LM']   
14331  ['maj_gemma-7b_LM', 'maj_llama2-13b-chat_CHAT'...   

                                        prediction  
14327  ['maj_gemma-7b_LM', 'maj_mistral-7b-lm_LM']  
14328  ['maj_gemma-7b_LM', 'maj_mistral-7b-lm_LM']  
14329  ['maj_gemma-7b_LM', 'maj_mistral-7b-lm_LM']  
14330  ['maj_gemma-7b_LM', 'maj_mistral-7b-lm_LM']  
14331  ['maj_gemma-7b_LM', 'maj_mistral-7b-lm_LM']

In [4]:
# find index of the element will all 1, to automatically obatined correct LLM mapping
def clean(labels, flag):
    if flag == 'conf':
        elabels = [list(map(float, re.findall(r'-?\d+(?:\.\d+)?(?:[eE][+\-]?\d+)?', s))) for s in labels]
    else:
        elabels = [list(map(int, item.strip('[]').split(' '))) for item in labels]    
    return elabels


def find_index_of_all_ones(lst):
    indices = []
    for i, sub_lst in enumerate(lst):
        if all(element == 1 for element in sub_lst):
            indices.append(i)
    return indices

pred_temp =  clean(data_all['raw_predictions'].tolist(), 'pred')
indices = find_index_of_all_ones(pred_temp)
print(pred_temp[indices[0]])

[1, 1, 1, 1, 1, 1, 1]


In [5]:
def mostfreqentval(mylist):
    if data_name == "gsm8k":
        my_list = [ float(item) for item in mylist if item != "INVALID"]
        
        counter = Counter(my_list)

        # Find the most common elements and their counts
        most_common_values = counter.most_common()
        if len(most_common_values) == 0:
            return 0.9999989898999998989899
        else:
            return most_common_values[0][0]
    elif data_name == "mmlu":
        my_list = [ item.strip() for item in mylist]
        
        counter = Counter(my_list)

        # Find the most common elements and their counts
        most_common_values = counter.most_common()
        if len(most_common_values) == 0:
            return 'jbdsijnofnqnnglnnkjer'
        else:
            return most_common_values[0][0]

In [6]:
#change as per the need
if data_name == 'gsm8k':
    llms = eval(data_all['prediction'].values.tolist()[indices[0]])
    print(llms)
    print(data_all['raw_predictions'].values.tolist()[indices[0]])
    id2mod = {i:val for i, val in enumerate(llms)}
    mod2id = {val:i for i, val in enumerate(llms)}
    mod2lat = {'maj_gemma-7b-it_CHAT':0.7,  'maj_gemma-7b_LM':7.1, 'maj_llama2-13b-chat_CHAT':1.8, 'maj_metamath-7b_LM':4.7, 'maj_mistral-7b-inst_CHAT':1.0, 'maj_mistral-7b-lm_LM':3.7}
elif data_name == 'mmlu':
    llms = eval(data_all['prediction'].values.tolist()[indices[0]])
    print(llms)
    print(data_all['raw_predictions'].values.tolist()[indices[0]])
    id2mod = {i:val for i, val in enumerate(llms)}
    mod2id = {val:i for i, val in enumerate(llms)}
    mod2lat = {'maj_gemma-7b-it_CHAT':1.0,  "maj_llama2-7b-lm_LM":2.3, 'maj_gemma-7b_LM':3.0, 'maj_llama2-13b-chat_CHAT':4.8, 'maj_metamath-7b_LM':2.4, 'maj_mistral-7b-inst_CHAT':1.1, 'maj_mistral-7b-lm_LM':1.8}
    
print(id2mod)
print(mod2id)

['maj_gemma-7b-it_CHAT', 'maj_gemma-7b_LM', 'maj_llama2-13b-chat_CHAT', 'maj_llama2-7b-lm_LM', 'maj_metamath-7b_LM', 'maj_mistral-7b-inst_CHAT', 'maj_mistral-7b-lm_LM']
[1 1 1 1 1 1 1]
{0: 'maj_gemma-7b-it_CHAT', 1: 'maj_gemma-7b_LM', 2: 'maj_llama2-13b-chat_CHAT', 3: 'maj_llama2-7b-lm_LM', 4: 'maj_metamath-7b_LM', 5: 'maj_mistral-7b-inst_CHAT', 6: 'maj_mistral-7b-lm_LM'}
{'maj_gemma-7b-it_CHAT': 0, 'maj_gemma-7b_LM': 1, 'maj_llama2-13b-chat_CHAT': 2, 'maj_llama2-7b-lm_LM': 3, 'maj_metamath-7b_LM': 4, 'maj_mistral-7b-inst_CHAT': 5, 'maj_mistral-7b-lm_LM': 6}


In [7]:
# Collecting ground Truth, Predictions, and confidence scores
Global_List = []        

truth = [ [1 if element in item else 0 for element in llms]  for item in data['true_label'].tolist()]
pred = [ [1 if element in item else 0 for element in llms]  for item in data['prediction'].tolist()]

pred_check =  clean(data['raw_predictions'].tolist(), 'pred')
raw_conf = clean(data['confidence'].tolist(), 'conf')
gold_ans = data['gold_answer'].tolist()

assert len(truth) == len(pred) == len(pred_check) == len(raw_conf) == len(gold_ans)
for p, pc in zip(pred, pred_check):
    if p != pc:
        print(p,pc)

print("Length of the Test Set:", len(pred))
print("Ground Truth Sample:", truth[:2])
print("Predictions Sample:", pred[:2])
print("Confidence Sample:", raw_conf[:2])
print("Gold Answers:", gold_ans[:2])
print("Model Details:", llms)

sample_answers = {}
for i, name in enumerate(llms):
    sample_answers[str(name)] = [eval(item) for item in data["auto_answers_"+str(name)].values.tolist()]
    assert len(sample_answers[str(name)]) == len(pred)
    print(f"The sample all answers for {name}LLM is:", sample_answers[str(name)][:2])


Global_List.append(['Considered LLMs', llms, '-', '-'])
Global_List.append(['Considered #LLMs', len(llms), '-', '-'])

Length of the Test Set: 1530
Ground Truth Sample: [[1, 1, 0, 1, 0, 1, 0], [1, 0, 0, 0, 1, 0, 0]]
Predictions Sample: [[0, 1, 0, 0, 0, 0, 1], [0, 1, 0, 0, 0, 0, 1]]
Confidence Sample: [[-0.15058538, 0.42898753, -0.11417119, -0.3520074, -0.62594503, -0.12832004, 0.35829893], [-0.21105905, 0.32114264, -0.20708264, -0.42240465, -0.66034776, -0.24259302, 0.2743512]]
Gold Answers: ['A', 'B']
Model Details: ['maj_gemma-7b-it_CHAT', 'maj_gemma-7b_LM', 'maj_llama2-13b-chat_CHAT', 'maj_llama2-7b-lm_LM', 'maj_metamath-7b_LM', 'maj_mistral-7b-inst_CHAT', 'maj_mistral-7b-lm_LM']
The sample all answers for maj_gemma-7b-it_CHATLLM is: [['A', 'B', 'A', 'A', 'A', 'B', 'B', 'B', 'B', 'A'], ['A', 'B', 'B', 'A', 'A', 'B', 'B', 'D', 'A', 'B']]
The sample all answers for maj_gemma-7b_LMLLM is: [['C', 'D', 'B', 'A', 'A', 'C', 'A', 'A', 'D', 'D'], ['INVALID', 'A', 'D', 'A', 'A', 'A', 'B', 'A', 'D', 'A']]
The sample all answers for maj_llama2-13b-chat_CHATLLM is: [['D', 'C', 'C', 'C', 'C', 'C', 'D', 'D', 'D', 

In [8]:
#classification report
from sklearn.metrics import classification_report
print(classification_report(truth, pred, target_names=llms))
Global_List.append(['Classifier-f1-weighted', f1_score(truth, pred, average='weighted'), '-', '-'])

                          precision    recall  f1-score   support

    maj_gemma-7b-it_CHAT       0.60      0.67      0.63       776
         maj_gemma-7b_LM       0.64      1.00      0.78       975
maj_llama2-13b-chat_CHAT       0.60      0.83      0.70       810
     maj_llama2-7b-lm_LM       0.63      0.59      0.61       736
      maj_metamath-7b_LM       0.57      0.49      0.53       639
maj_mistral-7b-inst_CHAT       0.61      0.81      0.70       825
    maj_mistral-7b-lm_LM       0.62      1.00      0.76       942

               micro avg       0.61      0.79      0.69      5703
               macro avg       0.61      0.77      0.67      5703
            weighted avg       0.61      0.79      0.68      5703
             samples avg       0.57      0.67      0.57      5703



/home/kaushal.maurya/miniconda3/envs/pds_py310/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in samples with no true labels. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


In [9]:
import numpy as np
import math

def softmax_manual(scores):
    exp_scores = np.exp(scores - np.max(scores))
    return exp_scores / exp_scores.sum(axis=0)

def sigmoid(scores):
    return [(1 / (1 + math.exp(-x))) for x in scores]


conf = [sigmoid(item) for item in raw_conf]
print("Confidence Sample:", conf[:5])

Confidence Sample: [[0.46242463296235675, 0.6056318740463404, 0.47148816689633527, 0.41289571660162994, 0.34843055756810076, 0.4679639368461123, 0.5886285906998269], [0.44743024014092503, 0.5796026970045475, 0.44841355777114544, 0.39594148193783224, 0.3406614964156547, 0.43964744100177794, 0.5681608047800245], [0.43251652408064595, 0.5263038387405934, 0.44514623410603515, 0.40806425267933427, 0.342109899015884, 0.42993440809189715, 0.5039069254829919], [0.44842741125954066, 0.5609822007354336, 0.4381628805976782, 0.39546826089345033, 0.3420310993630993, 0.42993468014272057, 0.5423343754461152], [0.4370958469364116, 0.5618603435267621, 0.4520502473852449, 0.40348013230585383, 0.3448959862957099, 0.4491010599964483, 0.5567503674093514]]


In [10]:
from collections import Counter

def lab_dist(all_in):
    temp = [ [ id2mod[i] for i, val in enumerate(item) if val !=0 ] for item in all_in]
    flattened_list = [item for sublist in temp for item in sublist]

    # Count the occurrences of each element
    element_counts = Counter(flattened_list)
    # Display the counts
    for element, count in element_counts.items():
        percentage = (count / len(all_in)) * 100
        print(f"{element}: {count} times ({percentage:.2f}%)")
    return element_counts

print("*********** Ground Truth Label Distribution *************")
truth_dist = lab_dist(truth)
print("")
print("*********** Prediction Label Distribution ****************")
pred_dist = lab_dist(pred)

*********** Ground Truth Label Distribution *************
maj_gemma-7b-it_CHAT: 776 times (50.72%)
maj_gemma-7b_LM: 975 times (63.73%)
maj_llama2-7b-lm_LM: 736 times (48.10%)
maj_mistral-7b-inst_CHAT: 825 times (53.92%)
maj_metamath-7b_LM: 639 times (41.76%)
maj_mistral-7b-lm_LM: 942 times (61.57%)
maj_llama2-13b-chat_CHAT: 810 times (52.94%)

*********** Prediction Label Distribution ****************
maj_gemma-7b_LM: 1530 times (100.00%)
maj_mistral-7b-lm_LM: 1524 times (99.61%)
maj_gemma-7b-it_CHAT: 863 times (56.41%)
maj_llama2-13b-chat_CHAT: 1116 times (72.94%)
maj_llama2-7b-lm_LM: 691 times (45.16%)
maj_metamath-7b_LM: 550 times (35.95%)
maj_mistral-7b-inst_CHAT: 1103 times (72.09%)


In [11]:
def get_maj_accuracy_all(baseconfg):
    collect_llms = [str(id2mod[item-1]) for item in baseconfg]

    maj_count = 0
    collect_acc, all_collect_llms = [], []
    for i, item in enumerate(sample_answers[collect_llms[0]]):
        all_collect_llms.append(collect_llms)
        all_auto_ans = [sample_answers[llm_name][i] for llm_name in collect_llms]
        flat_all_auto_ans = [item for sublist in all_auto_ans for item in sublist]
        
        if data_name == 'gsm8k':
            gold_llm_ans = float(gold_ans[i])
            pred_llm_ans = float(mostfreqentval(flat_all_auto_ans))
        elif data_name == 'mmlu':
            gold_llm_ans = gold_ans[i].strip()
            pred_llm_ans = mostfreqentval(flat_all_auto_ans).strip()
            
        if gold_llm_ans == pred_llm_ans:
            maj_count += 1
            collect_acc.append(1)
        else:
            collect_acc.append(0)
        
    return maj_count/len(sample_answers[collect_llms[0]]), collect_acc, all_collect_llms

In [12]:
print("********** Running Orecle Model *********")
# Oracle Model: Always selct best model
def oreacle(all_lab):
    acc_count = 0
    temp_count = 0
    llm_count = len(llms)*[0]
    for lab in all_lab:
        for i, val in enumerate(lab):
            if val == 1:
                acc_count += 1
                llm_count[i] += 1
                break
            if i ==len(llms)-1:
                temp_count += 1 
   
    assert temp_count + sum(llm_count) == len(all_lab)
    return acc_count, llm_count
        

acc, llm_count_list = oreacle(truth)
facc = acc/(len(truth))
lat = sum([ item* mod2lat[id2mod[i]] for i, item in enumerate(llm_count_list)])
flat=lat/sum(llm_count_list)


#best oracle values with maj_voates - This will be constent
from itertools import combinations

def generate_combinations(n):
    # Create a list of numbers from 1 to n
    numbers = list(range(1, n + 1))
    # Initialize an empty list to store combinations
    all_combinations = []
    # Generate combinations of different lengths
    for r in range(1, n + 1):
        # Use itertools.combinations to generate combinations of length r
        combinations_r = list(combinations(numbers, r))
        # Extend the list of all combinations
        all_combinations.extend(combinations_r)
    return all_combinations

def best_models(all_models):
    collect_all_model_acc, collect_lat = [],[]
    for item in all_models:
        collect_lat.extend([mod2lat[str(id2mod[val-1])] for val in item])
        collect_all_model_acc.append(get_maj_accuracy_all(item))
    
    max_acc = max(collect_all_model_acc)
    max_acc_models_index = collect_all_model_acc.index(max_acc)
    max_acc_models_name = [ id2mod[mod-1] for mod in all_models[max_acc_models_index]]
    print("Models Are: ", max_acc_models_name)
    return max_acc, sum(collect_lat) 


all_models = [ list(item) for item in generate_combinations(len(llms))]
all_models_max_acc, total_lat = best_models(all_models)
print("Total Number of models :", len(all_models))
print("Max Accuracy (%) : ", facc*100)
print("Max Accuracy with Maj (%) : ", all_models_max_acc*100)
print("Min Latency (Sec/Prompt) : ", flat)
print("Total Latency with Maj (Sec/Prompt) : ", total_lat)
Global_List.append(['Overall Oracle', "--", all_models_max_acc*100, total_lat])

********** Running Orecle Model *********
Models Are:  ['maj_gemma-7b_LM', 'maj_mistral-7b-lm_LM']
Total Number of models : 127
Max Accuracy (%) :  89.281045751634
Max Accuracy with Maj (%) :  (0.657516339869281, [1, 0, 1, 1, 1, 0, 1, 0, 0, 1, 0, 1, 0, 1, 1, 1, 0, 1, 1, 0, 1, 0, 0, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 0, 0, 1, 1, 1, 0, 1, 1, 1, 0, 1, 0, 0, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 1, 1, 0, 0, 1, 1, 0, 1, 0, 1, 1, 0, 0, 1, 1, 1, 1, 0, 0, 0, 1, 0, 0, 0, 0, 1, 0, 1, 1, 0, 1, 0, 0, 0, 1, 0, 1, 1, 1, 0, 0, 0, 0, 1, 0, 1, 0, 1, 0, 1, 0, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 1, 1, 0, 0, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 0, 0, 0, 1, 1, 1, 1, 1, 1, 0, 1, 0, 0, 1, 1, 0, 1, 0, 1, 1, 0, 1, 1, 1, 1, 1, 1, 0, 1, 1, 0, 1, 0, 1, 1, 0, 1, 0, 0, 1, 1, 0, 0, 1, 1, 0, 1, 1, 1, 1, 0, 0, 0, 1, 1, 0, 1, 0, 1, 1, 0, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 0, 1, 1, 1, 1, 0, 1, 1, 1, 0, 1, 0, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 0, 1, 1, 1, 

In [ ]:
print("********** Running Query-Aware Orecle Model *********")
#best oracle values with maj_voates - This will be constent
from itertools import combinations

def generate_combinations(n):
    # Create a list of numbers from 1 to n
    numbers = list(range(1, n + 1))
    # Initialize an empty list to store combinations
    all_combinations = []
    # Generate combinations of different lengths
    for r in range(1, n + 1):
        # Use itertools.combinations to generate combinations of length r
        combinations_r = list(combinations(numbers, r))
        # Extend the list of all combinations
        all_combinations.extend(combinations_r)
    return all_combinations


all_models = [ list(item) for item in generate_combinations(len(llms))]

maj_count, maj_lat = 0, 0
used_llms, used_llms_len = [],[]
for i, item in enumerate(sample_answers[llms[0]]):
    for j, model in enumerate(all_models):
        collect_llms = [str(id2mod[item-1]) for item in model]
        all_auto_ans = [sample_answers[llm_name][i] for llm_name in collect_llms]
        flat_all_auto_ans = [item for sublist in all_auto_ans for item in sublist]

        if data_name == 'gsm8k':
            gold_llm_ans = float(gold_ans[i])
            pred_llm_ans = float(mostfreqentval(flat_all_auto_ans))
        elif data_name == 'mmlu':
            gold_llm_ans = gold_ans[i].strip()
            pred_llm_ans = mostfreqentval(flat_all_auto_ans).strip()

        if gold_llm_ans == pred_llm_ans:
            maj_count += 1
            used_llms.append(collect_llms)
            used_llms_len.append(len(collect_llms))
            maj_lat = maj_lat + sum([mod2lat[llm] for llm in collect_llms])
            break

        if j == len(all_models) -1:
            used_llms.append([])
            used_llms_len.append(0)

all_models_max_acc, total_lat = maj_count/(len(sample_answers[llms[0]])), maj_lat/(len(sample_answers[llms[0]]))

print("Total Number of models :", len(all_models))
print("Max Accuracy with Maj (%) : ", all_models_max_acc*100)
print("Total Latency with Maj (Sec/Prompt) : ", total_lat)
Global_List.append(['Overall Oracle', "--", all_models_max_acc*100, total_lat])

print("*********** Oracle LLMs Distribution ****************")
flat_selectllm = [item for sublist in used_llms for item in sublist]
percentage_selectllm = {key: (value / len(flat_selectllm)) * 100 for key, value in Counter(flat_selectllm).items()}
print(percentage_selectllm)

print("*********** Oracle LLM's Length Distribution ****************")
percentage_distribution = {key: (value / len(used_llms_len)) * 100 for key, value in Counter(used_llms_len).items()}
print(percentage_distribution)

data_test["Oracle"] = used_llms
data_test["Oracle_lab"] = [1 if len(item) else 0 for item in used_llms]
data_test.head()

In [14]:
print("********** Running Individual Baseline Models *********")
# Oracle Model: Always selct best model
def baseline(all_lab):
    acc_count = 0
    temp_count = 0
    llm_count = len(llms)*[0]
    for lab in all_lab:
        for i, val in enumerate(lab):
            if val == 1:
                acc_count += 1
                llm_count[i] += 1
                break
            if i ==len(llms)-1:
                temp_count += 1 
   
    assert temp_count + sum(llm_count) == len(all_lab)
    return acc_count, llm_count
        
def all_baselines(filtered_truth):
    acc, llm_count_list = baseline(filtered_truth)
    facc = acc/(len(truth))
    lat = sum([ item*mod2lat[id2mod[i]] for i, item in enumerate(llm_count_list)])
    flat=0
    return facc, flat


baseline_config = [[i+1] for i, item in enumerate(llms)]
print("Configurations:", baseline_config)
    
for base in baseline_config:
    out_maj, _, _ = get_maj_accuracy_all(base)
    out_lat_maj =mod2lat[id2mod[base[0]-1]]
    filt_truth = [[val if i in base else 0 for i, val in enumerate(item)] for item in truth]
    out_acc, out_lat = all_baselines(filt_truth)
    Global_List.append([[id2mod[ind-1] for ind in base], "--", out_maj*100,  out_lat_maj])
    print("Current Model is/are:",  [ id2mod[ind-1] for ind in base])
    print("Max Accuracy (%) : ", out_maj*100)
    print("Latency (Sec/Prompt) : ", float(out_lat_maj))

********** Running Individual Baseline Models *********
Configurations: [[1], [2], [3], [4], [5], [6], [7]]
Current Model is/are: ['maj_gemma-7b-it_CHAT']
Max Accuracy (%) :  50.71895424836601
Latency (Sec/Prompt) :  1.0
Current Model is/are: ['maj_gemma-7b_LM']
Max Accuracy (%) :  63.725490196078425
Latency (Sec/Prompt) :  3.0
Current Model is/are: ['maj_llama2-13b-chat_CHAT']
Max Accuracy (%) :  52.94117647058824
Latency (Sec/Prompt) :  4.8
Current Model is/are: ['maj_llama2-7b-lm_LM']
Max Accuracy (%) :  48.10457516339869
Latency (Sec/Prompt) :  2.3
Current Model is/are: ['maj_metamath-7b_LM']
Max Accuracy (%) :  41.76470588235294
Latency (Sec/Prompt) :  2.4
Current Model is/are: ['maj_mistral-7b-inst_CHAT']
Max Accuracy (%) :  53.92156862745098
Latency (Sec/Prompt) :  1.1
Current Model is/are: ['maj_mistral-7b-lm_LM']
Max Accuracy (%) :  61.568627450980394
Latency (Sec/Prompt) :  1.8


In [ ]:
print("********** Running top-k Orecle Model *********")
#Models with best model combinations

def generate_combinations(n):
    # Create a list of numbers from 1 to n
    numbers = list(range(1, n + 1))
    # Initialize an empty list to store combinations
    all_combinations = []
    # Generate combinations of different lengths
    for r in range(1, n + 1):
        # Use itertools.combinations to generate combinations of length r
        combinations_r = list(combinations(numbers, r))
        # Extend the list of all combinations
        all_combinations.extend(combinations_r)
    return all_combinations

def best_k_models(all_models):
    collect_all_model_acc, collect_lat = [],[]
    for item in all_models:
        collect_lat.extend([mod2lat[str(id2mod[val-1])] for val in item])
        collect_all_model_acc.append(get_maj_accuracy_all(item))
    
    max_acc = max(collect_all_model_acc)
    max_acc_models_index = collect_all_model_acc.index(max_acc)
    max_acc_models_name = [ id2mod[mod-1] for mod in all_models[max_acc_models_index]]
    print("Models Are: ", max_acc_models_name)
    return max_acc, sum(collect_lat)
    

all_models = [ list(item) for item in generate_combinations(len(llms))]

for i in range(1, 1+len(llms)):
    print(f"======Basline with top {i} Model======")
    retain_models = [ item for item in all_models if len(item) <= i]
    k_max_acc, k_total_lat = best_k_models(retain_models)
    print("Max Accuracy (%) : ", facc*100)
    print("Max Accuracy with Maj (%) : ", k_max_acc*100)
    print("Min Latency (Sec/Prompt) : ", k_total_lat)
    Global_List.append([f'Oracle with top-{i} models', "--", k_max_acc*100, k_total_lat ])

In [ ]:
print("********** Running best k performing Model *********")
from collections import Counter

sorted_dict = dict(sorted(truth_dist.items(), key=lambda item: item[1], reverse=True))
topk_llms = list(sorted_dict.keys())
print("Top-k performing LLMs :", topk_llms)


for i in range(1, len(topk_llms) + 1):
    # collect_lat = []
    print(f"======Basline with top performing {i} Model======")
    print("Models:", topk_llms[:i])
    # for item in topk_llms[:i]:
    #     collect_lat.append(mod2lat[item])
    
    total_lat = sum([ mod2lat[llm] for llm in llms])
    
    maj_acc, acc_list, llm_list = get_maj_accuracy_all([mod2id[item]+1 for item in topk_llms[:i]])
    print("Max Accuracy with Maj (%) : ", maj_acc*100)
    print("Min Latency (Sec/Prompt) : ", total_lat)
    Global_List.append([f'Performance with top {i} LLMs', "--", maj_acc*100, total_lat ])

data_test["tops"] = llm_list
data_test["tops_lab"] = acc_list
data_test.head()

In [ ]:
print("********** Running Bottom-k performing Model *********")
from collections import Counter

sorted_dict = dict(sorted(truth_dist.items(), key=lambda item: item[1], reverse=True))
topk_llms = list(sorted_dict.keys())[::-1]
print("Bottom-k performing LLMs :", topk_llms)

for i in range(1, len(topk_llms) + 1):
    # collect_lat = []
    print(f"======Basline with bottom performing {i} Model======")
    print("Models:", topk_llms[:i])
    # for item in topk_llms[:i]:
    #     collect_lat.append(mod2lat[item])
    total_lat = sum([ mod2lat[llm] for llm in llms])
    
    maj_acc = get_maj_accuracy_all([mod2id[item]+1 for item in topk_llms[:i]])
    print("Max Accuracy with Maj (%) : ", maj_acc*100)
    print("Min Latency (Sec/Prompt) : ", total_lat)
    Global_List.append([f'Prformance with Bottom {i} LLMs', "--", maj_acc*100, total_lat ])

In [18]:
print("***********Running Random Baseline Model ************")
import random

all_models = [ list(item) for item in generate_combinations(len(llms))]

def get_random_baseline():
    maj_count, maj_lat = 0, 0
    for i, item in enumerate(sample_answers[llms[0]]):
        model  = random.choice(all_models)
        collect_llms = [str(id2mod[item-1]) for item in model]
        all_auto_ans = [sample_answers[llm_name][i] for llm_name in collect_llms]
        flat_all_auto_ans = [item for sublist in all_auto_ans for item in sublist]

        if data_name == 'gsm8k':
            gold_llm_ans = float(gold_ans[i])
            pred_llm_ans = float(mostfreqentval(flat_all_auto_ans))
        elif data_name == 'mmlu':
            gold_llm_ans = gold_ans[i].strip()
            pred_llm_ans = mostfreqentval(flat_all_auto_ans).strip()

        if gold_llm_ans == pred_llm_ans:
            maj_count += 1
            maj_lat = maj_lat + sum([mod2lat[llm] for llm in collect_llms])
        else:
            maj_lat = maj_lat + sum([mod2lat[llm] for llm in collect_llms])

    return maj_count/(len(sample_answers[llms[0]])), maj_lat/(len(sample_answers[llms[0]]))

sampling = 1000
acc_list, lat_list = [],[]
for k in range(sampling):
    maj_acc, maj_lat = get_random_baseline()
    acc_list.append(maj_acc)
    lat_list.append(maj_lat)

assert len(acc_list) == len(lat_list)
avg_acc = sum(acc_list)/sampling
avg_lat = sum(lat_list)/sampling
print("Accuracy: ", avg_acc*100)
print("Latency (Sec/Prompt) : ", avg_lat)
Global_List.append([f'Random baseline models', "--", avg_acc*100, avg_lat])

***********Running Random Baseline Model ************
Accuracy:  58.167647058823505
Latency (Sec/Prompt) :  8.263806993464064


In [19]:
print("******* Policy-1: Classifer's Upper Bound ******")
# this will be calculated with with function as = f(prediction, ground truth, confidence)
        
def top_k_indices(input_list, confidence_list, k):
    # Zip the input list and confidence list together
    zipped_data = list(zip(input_list, confidence_list))
    
    # Filter elements where value in input list is 1
    filtered_data = [(idx, conf) for idx, (val, conf) in enumerate(zipped_data) if val == 1]
    
    # Sort filtered elements based on confidence scores in descending order
    sorted_data = sorted(filtered_data, key=lambda x: x[1], reverse=True)
    
    # Extract top k indices
    top_indices = [idx for idx, _ in sorted_data[:k]]
    
    return top_indices
    
def selectLLM_models_upperbound(pred_list, conf_list):
    collect_acc, total_lat = 0, 0 
    selected_models, selected_models_len = [], []
    for i, (pred, conf) in enumerate(zip(pred_list, conf_list)):
        output_list = [top_k_indices(pred, conf, llm_indx+1) for llm_indx, _ in enumerate(llms)]
        
        flag = 0
        for j, out in enumerate(output_list):
            collect_llms = [str(id2mod[item]) for item in out]
            all_auto_ans = [sample_answers[llm_name][i] for llm_name in collect_llms]
            flat_all_auto_ans = [item for sublist in all_auto_ans for item in sublist]
        
            if data_name == 'gsm8k':
                gold_llm_ans = float(gold_ans[i])
                pred_llm_ans = float(mostfreqentval(flat_all_auto_ans))
            elif data_name == 'mmlu':
                gold_llm_ans = gold_ans[i].strip()
                pred_llm_ans = mostfreqentval(flat_all_auto_ans).strip()
            
            if gold_llm_ans == pred_llm_ans:
                flag = 1
                selected_models.append(collect_llms)
                selected_models_len.append(len(collect_llms))
                total_lat = total_lat + sum([mod2lat[item] for item in collect_llms])
                break
            elif j == len(output_list)-1:
                selected_models.append([])
                selected_models_len.append(0)

                
        if flag == 1:
            collect_acc += 1
    return collect_acc/len(pred_list), total_lat/len(pred_list), selected_models, selected_models_len
                
    
maj_acc, maj_lat, selectllm, selectllm_len = selectLLM_models_upperbound(pred, conf)
print(len(pred), len(conf))

print("Accuracy with Maj: ", maj_acc*100)
print("Latency (Sec/Prompt) : ", maj_lat)

print("*********** SelectLLM Model Distribution ****************")
flat_selectllm = [item for sublist in selectllm for item in sublist]
percentage_selectllm = {key: (value / len(flat_selectllm)) * 100 for key, value in Counter(flat_selectllm).items()}
print(percentage_selectllm)
print("*********** SelectLLM Model Length Distribution ****************")
percentage_distribution = {key: (value / len(selectllm_len)) * 100 for key, value in Counter(selectllm_len).items()}
print(percentage_distribution)

Global_List.append(['Policy-1: Uppercound (Classifier) :', "--", maj_acc*100, maj_lat])

# data_test["ClassUpperBound"] = selectllm
# data_test.head()

******* Policy-1: Classifer's Upper Bound ******
1530 1530
Accuracy with Maj:  74.05228758169935
Latency (Sec/Prompt) :  2.5479084967320302
*********** SelectLLM Model Distribution ****************
{'maj_gemma-7b_LM': 81.49492017416546, 'maj_mistral-7b-lm_LM': 11.828737300435414, 'maj_mistral-7b-inst_CHAT': 3.0478955007256894, 'maj_llama2-13b-chat_CHAT': 2.539912917271408, 'maj_gemma-7b-it_CHAT': 0.7256894049346879, 'maj_llama2-7b-lm_LM': 0.21770682148040638, 'maj_metamath-7b_LM': 0.14513788098693758}
*********** SelectLLM Model Length Distribution ****************
{1: 63.464052287581694, 0: 25.947712418300657, 2: 7.38562091503268, 3: 1.7647058823529411, 5: 0.261437908496732, 4: 0.9803921568627451, 6: 0.065359477124183, 7: 0.130718954248366}


In [ ]:
print("******* Policy-1: Select LLM Models ******")

def top_k_indices_old(numbers, k):
    # Enumerate the numbers with their indices
    indexed_numbers = list(enumerate(numbers))
    # Sort the indexed numbers based on their values
    sorted_numbers = sorted(indexed_numbers, key=lambda x: x[1], reverse=True)
    # Get the indices of the top k elements
    top_indices = [index for index, _ in sorted_numbers[:k]]
    return top_indices

def get_maj_accuracy_single(baseconfg, inx):
    collect_llms = [str(id2mod[item]) for item in baseconfg]
    all_auto_ans = [sample_answers[llm_name][inx] for llm_name in collect_llms]
    flat_all_auto_ans = [item for sublist in all_auto_ans for item in sublist]
    
    if data_name == 'gsm8k':
        gold_llm_ans = float(gold_ans[inx])
        pred_llm_ans = float(mostfreqentval(flat_all_auto_ans))
    elif data_name == 'mmlu':
        gold_llm_ans = gold_ans[inx].strip()
        pred_llm_ans = mostfreqentval(flat_all_auto_ans).strip()

    if gold_llm_ans == pred_llm_ans:
        return 1
    else:
        return 0
    
def policy5(pred_list, conf_list, truth_list, top):
    acc_count, temp_count, maj_count = 0, 0, 0
    llm_count = len(llms)*[0]
    for i, (p, c, t) in enumerate(zip(pred_list, conf_list, truth_list)):
        top_indx = top_k_indices_old(c, top)
        if get_maj_accuracy_single(top_indx, i) == 1:
            maj_count += 1
        
        success = 0 
        for indx in top_indx:
            if p[indx] == 1 and t[indx] == 1:
                success = 1
                llm_count[indx] += 1
                
        if success == 1:
            acc_count += 1 

    return acc_count, llm_count, maj_count
    
def top_k_indices(input_list, confidence_list, k):
    # Zip the input list and confidence list together
    zipped_data = list(zip(input_list, confidence_list))
    
    # Filter elements where value in input list is 1
    filtered_data = [(idx, conf) for idx, (val, conf) in enumerate(zipped_data) if val == 1]
    
    # Sort filtered elements based on confidence scores in descending order
    sorted_data = sorted(filtered_data, key=lambda x: x[1], reverse=True)
    
    # Extract top k indices
    top_indices = [idx for idx, _ in sorted_data[:k]]
    
    return top_indices
    
def selectLLM(pred_list, conf_list, top):
    collect_acc, total_lat = 0, 0 
    selected_models, selected_models_len, lab_list = [], [], []
    for i, (pred, conf) in enumerate(zip(pred_list, conf_list)):
        output_list = top_k_indices(pred, conf, top)
        if len(output_list) != 0:
            collect_llms = [str(id2mod[item]) for item in output_list]
            all_auto_ans = [sample_answers[llm_name][i] for llm_name in collect_llms]
            flat_all_auto_ans = [item for sublist in all_auto_ans for item in sublist]

            selected_models.append(collect_llms)
            selected_models_len.append(len(collect_llms))
            total_lat = total_lat + sum([mod2lat[item] for item in collect_llms])

            if data_name == 'gsm8k':
                gold_llm_ans = float(gold_ans[i])
                pred_llm_ans = float(mostfreqentval(flat_all_auto_ans))
            elif data_name == 'mmlu':
                gold_llm_ans = gold_ans[i].strip()
                pred_llm_ans = mostfreqentval(flat_all_auto_ans).strip()

            if gold_llm_ans == pred_llm_ans:
                collect_acc += 1
                lab_list.append(1)
            else:
                lab_list.append(0)
        else:
            lab_list.append(1)
        
            
    return collect_acc/len(pred_list), total_lat/len(pred_list), selected_models, selected_models_len, lab_list
        

for i in range(len(llms)):
    print("*"*100)
    print(f"====== SelectLLM with {i+1} LLMS ======")
    print("*"*100)
    maj, maj_lat, selectllm, selectllm_len, lab_list_ = selectLLM(pred, conf, i+1)
    
    acc, llm_count_list, maj_old = policy5(pred, conf, truth, i+1)
    facc = acc/(len(truth))
    fmaj = maj_old/(len(truth))
    lat = sum([ item*mod2lat[id2mod[i]] for i, item in enumerate(llm_count_list)])
    flat=lat/sum(llm_count_list)
    
    print("Accuracy (%): ", facc*100)
    print("Accuracy with Maj(%): ", maj*100)
    print("Latency with Maj(Sec/Prompt) : ", maj_lat)
    
    print("*********** SelectLLM Model Distribution ****************")
    flat_selectllm = [item for sublist in selectllm for item in sublist]
    percentage_selectllm = {key: (value / len(flat_selectllm)) * 100 for key, value in Counter(flat_selectllm).items()}
    print(percentage_selectllm)

    print("*********** SelectLLM Model Length Distribution ****************")
    percentage_distribution = {key: (value / len(selectllm_len)) * 100 for key, value in Counter(selectllm_len).items()}
    print(percentage_distribution)
    Global_List.append([f' Policy1: SelectLLM with {i+1} LLMS', "--", maj*100, maj_lat])

    if (i+1) == 2:
        data_test["policy1"] = selectllm
        data_test["policy1_lab"] = lab_list_
        data_test.head()

In [21]:
data_test.head()

question  \
14327  The cyclic subgroup of Z_24 generated by 18 ha...   
14328  Find the order of the factor group Z_6/<3>. (A...   
14329  Statement 1 | A permutation that is a product ...   
14330  Find the order of the factor group (Z_4 x Z_12...   
14331  Find the maximum possible order for some eleme...   

                                              true_label  \
14327  ['maj_gemma-7b-it_CHAT', 'maj_gemma-7b_LM', 'm...   
14328     ['maj_gemma-7b-it_CHAT', 'maj_metamath-7b_LM']   
14329  ['maj_gemma-7b-it_CHAT', 'maj_gemma-7b_LM', 'm...   
14330                           ['maj_mistral-7b-lm_LM']   
14331  ['maj_gemma-7b_LM', 'maj_llama2-13b-chat_CHAT'...   

                                        prediction                  Oracle  \
14327  ['maj_gemma-7b_LM', 'maj_mistral-7b-lm_LM']  [maj_gemma-7b-it_CHAT]   
14328  ['maj_gemma-7b_LM', 'maj_mistral-7b-lm_LM']  [maj_gemma-7b-it_CHAT]   
14329  ['maj_gemma-7b_LM', 'maj_mistral-7b-lm_LM']  [maj_gemma-7b-it_CHAT]   
14330  ['maj_gemma-7b_LM', 'maj_mistral-7b-lm_LM']  [maj_mistral-7b-lm_LM]   
14331  ['maj_gemma-7b_LM', 'maj_mistral-7b-lm_LM']       [maj_gemma-7b_LM]   

       Oracle_lab                                               tops  \
14327           1  [maj_gemma-7b_LM, maj_mistral-7b-lm_LM, maj_mi...   
14328           1  [maj_gemma-7b_LM, maj_mistral-7b-lm_LM, maj_mi...   
14329           1  [maj_gemma-7b_LM, maj_mistral-7b-lm_LM, maj_mi...   
14330           1  [maj_gemma-7b_LM, maj_mistral-7b-lm_LM, maj_mi...   
14331           1  [maj_gemma-7b_LM, maj_mistral-7b-lm_LM, maj_mi...   

       tops_lab                                  policy1  policy1_lab  
14327         1  [maj_gemma-7b_LM, maj_mistral-7b-lm_LM]            1  
14328         0  [maj_gemma-7b_LM, maj_mistral-7b-lm_LM]            0  
14329         1  [maj_gemma-7b_LM, maj_mistral-7b-lm_LM]            1  
14330         0  [maj_gemma-7b_LM, maj_mistral-7b-lm_LM]            1  
14331         1  [maj_gemma-7b_LM, maj_mistral-7b-lm_LM]            1

In [22]:
print("******* Policy-2 (confidance only): Classifer's Upper Bound ******")
# this will be calculated with with function as = f(prediction, ground truth, confidence)
        
def top_k_indices(input_list, confidence_list, k):
    # Zip the input list and confidence list together
    zipped_data = list(zip(input_list, confidence_list))
    
    # Filter elements where value in input list is 1
    filtered_data = [(idx, conf) for idx, (val, conf) in enumerate(zipped_data)]
    
    # Sort filtered elements based on confidence scores in descending order
    sorted_data = sorted(filtered_data, key=lambda x: x[1], reverse=True)
    
    # Extract top k indices
    top_indices = [idx for idx, _ in sorted_data[:k]]
    
    return top_indices
    
def selectLLM_models_upperbound(pred_list, conf_list):
    collect_acc, total_lat = 0, 0 
    selected_models, selected_models_len, lab_list = [], [], []
    for i, (pred, conf) in enumerate(zip(pred_list, conf_list)):
        output_list = [top_k_indices(pred, conf, llm_indx+1) for llm_indx, _ in enumerate(llms)]
        
        flag = 0
        for out in output_list:
            collect_llms = [str(id2mod[item]) for item in out]
            all_auto_ans = [sample_answers[llm_name][i] for llm_name in collect_llms]
            flat_all_auto_ans = [item for sublist in all_auto_ans for item in sublist]
            
        
            if data_name == 'gsm8k':
                gold_llm_ans = float(gold_ans[i])
                pred_llm_ans = float(mostfreqentval(flat_all_auto_ans))
            elif data_name == 'mmlu':
                gold_llm_ans = gold_ans[i].strip()
                pred_llm_ans = mostfreqentval(flat_all_auto_ans).strip()
            
            if gold_llm_ans == pred_llm_ans:
                flag = 1
                selected_models.append(collect_llms)
                selected_models_len.append(len(collect_llms))
                lab_list.append(collect_llms)
                total_lat = total_lat + sum([mod2lat[item] for item in collect_llms])
                break
                
        if flag == 1:
            collect_acc += 1
            lab_list.append(1)
        else: 
            lab_list.append(0)
    return collect_acc/len(pred_list), total_lat/len(pred_list), selected_models, selected_models_len, lab_list
                
    
maj_acc, maj_lat, selectllm, selectllm_len, lab_list_ = selectLLM_models_upperbound(pred, conf)
# acc, llm_count_list = uperbound(truth, pred)
# facc = acc/(len(truth))
# print("Accuracy (%): ", facc*100)
# print("Accuracy with Maj: ", maj_acc*100)
# print("Latency (Sec/Prompt) : ", maj_lat)

print("*********** SelectLLM Model Distribution ****************")
flat_selectllm = [item for sublist in selectllm for item in sublist]
percentage_selectllm = {key: (value / len(flat_selectllm)) * 100 for key, value in Counter(flat_selectllm).items()}
print(percentage_selectllm)
print("*********** SelectLLM Model Length Distribution ****************")
percentage_distribution = {key: (value / len(selectllm_len)) * 100 for key, value in Counter(selectllm_len).items()}
print(percentage_distribution)

Global_List.append(['Policy-2: Uppercound (Classifier) :', "--", maj_acc*100, maj_lat])

******* Policy-2 (confidance only): Classifer's Upper Bound ******
*********** SelectLLM Model Distribution ****************
{'maj_gemma-7b_LM': 74.45721583652617, 'maj_mistral-7b-lm_LM': 13.154533844189018, 'maj_mistral-7b-inst_CHAT': 4.278416347381865, 'maj_llama2-13b-chat_CHAT': 4.789272030651341, 'maj_gemma-7b-it_CHAT': 2.10727969348659, 'maj_llama2-7b-lm_LM': 0.6385696040868455, 'maj_metamath-7b_LM': 0.5747126436781609}
*********** SelectLLM Model Length Distribution ****************
{1: 82.56802721088435, 2: 9.608843537414966, 3: 3.9115646258503403, 5: 1.445578231292517, 6: 0.25510204081632654, 4: 1.530612244897959, 7: 0.6802721088435374}


In [ ]:
print("******* Policy-2: Select LLM Models ******")

def top_k_indices_old(numbers, k):
    # Enumerate the numbers with their indices
    indexed_numbers = list(enumerate(numbers))
    # Sort the indexed numbers based on their values
    sorted_numbers = sorted(indexed_numbers, key=lambda x: x[1], reverse=True)
    # Get the indices of the top k elements
    top_indices = [index for index, _ in sorted_numbers[:k]]
    return top_indices

def get_maj_accuracy_single(baseconfg, inx):
    collect_llms = [str(id2mod[item]) for item in baseconfg]
    all_auto_ans = [sample_answers[llm_name][inx] for llm_name in collect_llms]
    flat_all_auto_ans = [item for sublist in all_auto_ans for item in sublist]
    
    if data_name == 'gsm8k':
        gold_llm_ans = float(gold_ans[inx])
        pred_llm_ans = float(mostfreqentval(flat_all_auto_ans))
    elif data_name == 'mmlu':
        gold_llm_ans = gold_ans[inx].strip()
        pred_llm_ans = mostfreqentval(flat_all_auto_ans).strip()

    if gold_llm_ans == pred_llm_ans:
        return 1
    else:
        return 0
    
def policy5(pred_list, conf_list, truth_list, top):
    acc_count, temp_count, maj_count = 0, 0, 0
    llm_count = len(llms)*[0]
    for i, (p, c, t) in enumerate(zip(pred_list, conf_list, truth_list)):
        top_indx = top_k_indices_old(c, top)
        if get_maj_accuracy_single(top_indx, i) == 1:
            maj_count += 1
        
        success = 0 
        for indx in top_indx:
            if p[indx] == 1 and t[indx] == 1:
                success = 1
                llm_count[indx] += 1
                
        if success == 1:
            acc_count += 1 

    return acc_count, llm_count, maj_count
    
def top_k_indices(input_list, confidence_list, k):
    # Zip the input list and confidence list together
    zipped_data = list(zip(input_list, confidence_list))
    
    # Filter elements where value in input list is 1
    filtered_data = [(idx, conf) for idx, (val, conf) in enumerate(zipped_data)]
    
    # Sort filtered elements based on confidence scores in descending order
    sorted_data = sorted(filtered_data, key=lambda x: x[1], reverse=True)
    
    # Extract top k indices
    top_indices = [idx for idx, _ in sorted_data[:k]]
    
    return top_indices
    
def selectLLM(pred_list, conf_list, top):
    collect_acc, total_lat = 0, 0 
    selected_models, selected_models_len, lab_list = [], [], []
    for i, (pred, conf) in enumerate(zip(pred_list, conf_list)):
        output_list = top_k_indices(pred, conf, top)

        if len(output_list) != 0:
            collect_llms = [str(id2mod[item]) for item in output_list]
            all_auto_ans = [sample_answers[llm_name][i] for llm_name in collect_llms]
            flat_all_auto_ans = [item for sublist in all_auto_ans for item in sublist]

            selected_models.append(collect_llms)
            selected_models_len.append(len(collect_llms))
            total_lat = total_lat + sum([mod2lat[item] for item in collect_llms])

            if data_name == 'gsm8k':
                gold_llm_ans = float(gold_ans[i])
                pred_llm_ans = float(mostfreqentval(flat_all_auto_ans))
            elif data_name == 'mmlu':
                gold_llm_ans = gold_ans[i].strip()
                pred_llm_ans = mostfreqentval(flat_all_auto_ans).strip()

            if gold_llm_ans == pred_llm_ans:
                collect_acc += 1
                lab_list.append(1)
            else:
                lab_list.append(0)
        else: 
            lab_list.append(0)
            
    return collect_acc/len(pred_list), total_lat/len(pred_list), selected_models, selected_models_len, lab_list
        

for i in range(len(llms)):
    print("*"*100)
    print(f"====== SelectLLM with {i+1} LLMS ======")
    print("*"*100)
    maj, maj_lat, selectllm, selectllm_len, lab_list_ = selectLLM(pred, conf, i+1)
    
    acc, llm_count_list, maj_old = policy5(pred, conf, truth, i+1)
    facc = acc/(len(truth))
    fmaj = maj_old/(len(truth))
    lat = sum([ item*mod2lat[id2mod[i]] for i, item in enumerate(llm_count_list)])
    flat=lat/sum(llm_count_list)
    
    print("Accuracy (%): ", facc*100)
    print("Accuracy with Maj(%): ", maj*100)
    print("Latency with Maj(Sec/Prompt) : ", maj_lat)
    
    print("*********** SelectLLM Model Distribution ****************")
    flat_selectllm = [item for sublist in selectllm for item in sublist]
    percentage_selectllm = {key: (value / len(flat_selectllm)) * 100 for key, value in Counter(flat_selectllm).items()}
    print(percentage_selectllm)

    print("*********** SelectLLM Model Length Distribution ****************")
    percentage_distribution = {key: (value / len(selectllm_len)) * 100 for key, value in Counter(selectllm_len).items()}
    print(percentage_distribution)
    Global_List.append([f' Policy2: SelectLLM with {i+1} LLMS', "--", maj*100, maj_lat])

    if (i+1) == 2:
        data_test["policy2"] = selectllm
        data_test["policy2_lab"] = lab_list_
        data_test.head()

In [24]:
print("******* Policy-3 (weighted confidance only): Classifer's Upper Bound ******")
# this will be calculated with with function as = f(prediction, ground truth, confidence)

from collections import Counter

def top_k_indices(input_list, confidence_list, k):
    # Zip the input list and confidence list together
    zipped_data = list(zip(input_list, confidence_list))
    
    # Filter elements where value in input list is 1
    filtered_data = [(idx, conf) for idx, (val, conf) in enumerate(zipped_data)]
    
    # Sort filtered elements based on confidence scores in descending order
    sorted_data = sorted(filtered_data, key=lambda x: x[1], reverse=True)
    
    # Extract top k indices
    top_indices = [(idx, con) for idx,con in sorted_data[:k]]
    
    return top_indices
    
def selectLLM_models_upperbound(pred_list, conf_list):
    collect_acc, total_lat = 0, 0 
    selected_models, selected_models_len = [], []
    for i, (pred, conf) in enumerate(zip(pred_list, conf_list)):
        output_list = [top_k_indices(pred, conf, llm_indx+1) for llm_indx, _ in enumerate(llms)]
        
        flag = 0
        for out in output_list:
            collect_llms = [str(id2mod[item[0]]) for item in out]
            collect_conf = {str(id2mod[item[0]]):item[1] for item in out}
            freq_dict = {str(llm_name):dict(Counter(sample_answers[llm_name][i])) for llm_name in collect_llms}
            weighted_freq_dict = {key: {subkey: value * collect_conf[key] for subkey, value in sublist.items()} for key, sublist in freq_dict.items()}
            
            merged = dict()
            for name, sublist in weighted_freq_dict.items():
                for key, values in sublist.items():
                    if key not in merged and key != "INVALID":
                        merged[key] = values
                    elif key != "INVALID":
                        merged[key] += values
            
            pred_llm_ans = max(merged, key=merged.get)
            
        
            if data_name == 'gsm8k':
                gold_llm_ans = float(gold_ans[i])
                pred_llm_ans = float(pred_llm_ans)
            elif data_name == 'mmlu':
                gold_llm_ans = gold_ans[i].strip()
                pred_llm_ans = pred_llm_ans.strip()
            
            if gold_llm_ans == pred_llm_ans:
                flag = 1
                selected_models.append(collect_llms)
                selected_models_len.append(len(collect_llms))
                total_lat = total_lat + sum([mod2lat[item] for item in collect_llms])
                break
                
        if flag == 1:
            collect_acc += 1
    return collect_acc/len(pred_list), total_lat/len(pred_list), selected_models, selected_models_len
                
    
maj_acc, maj_lat, selectllm, selectllm_len = selectLLM_models_upperbound(pred, conf)
# acc, llm_count_list = uperbound(truth, pred)
# facc = acc/(len(truth))
# print("Accuracy (%): ", facc*100)
print("Accuracy with Maj: ", maj_acc*100)
print("Latency (Sec/Prompt) : ", maj_lat)

print("*********** SelectLLM Model Distribution ****************")
flat_selectllm = [item for sublist in selectllm for item in sublist]
percentage_selectllm = {key: (value / len(flat_selectllm)) * 100 for key, value in Counter(flat_selectllm).items()}
print(percentage_selectllm)
print("*********** SelectLLM Model Length Distribution ****************")
percentage_distribution = {key: (value / len(selectllm_len)) * 100 for key, value in Counter(selectllm_len).items()}
print(percentage_distribution)

Global_List.append(['Policy-3: Uppercound (Classifier) :', "--", maj_acc*100, maj_lat])

******* Policy-3 (weighted confidance only): Classifer's Upper Bound ******
Accuracy with Maj:  76.20915032679738
Latency (Sec/Prompt) :  2.8018954248366046
*********** SelectLLM Model Distribution ****************
{'maj_gemma-7b_LM': 75.55555555555556, 'maj_mistral-7b-lm_LM': 12.745098039215685, 'maj_mistral-7b-inst_CHAT': 4.248366013071895, 'maj_llama2-13b-chat_CHAT': 4.509803921568627, 'maj_gemma-7b-it_CHAT': 1.9607843137254901, 'maj_llama2-7b-lm_LM': 0.522875816993464, 'maj_metamath-7b_LM': 0.4575163398692811}
*********** SelectLLM Model Length Distribution ****************
{1: 83.36192109777015, 2: 9.262435677530018, 3: 3.6020583190394513, 5: 1.3722126929674099, 4: 1.6295025728987993, 7: 0.5145797598627788, 6: 0.2572898799313894}


In [ ]:
print("******* Policy-3: Select LLM Models ******")

def top_k_indices(input_list, confidence_list, k):
    # Zip the input list and confidence list together
    zipped_data = list(zip(input_list, confidence_list))
    
    # Filter elements where value in input list is 1
    filtered_data = [(idx, conf) for idx, (val, conf) in enumerate(zipped_data)]
    
    # Sort filtered elements based on confidence scores in descending order
    sorted_data = sorted(filtered_data, key=lambda x: x[1], reverse=True)
    
    # Extract top k indices
    top_indices = [(idx, con) for idx,con in sorted_data[:k]]
    
    return top_indices
    
def selectLLM(pred_list, conf_list, top):
    collect_acc, total_lat = 0, 0 
    selected_models, selected_models_len, lab_list = [], [], []
    for i, (pred, conf) in enumerate(zip(pred_list, conf_list)):
        output_list = [top_k_indices(pred, conf, top) for llm_indx, _ in enumerate(llms)]

        if len(output_list) != 0:
            collect_llms = [str(id2mod[item[0]]) for item in output_list[0]]
            collect_conf = {str(id2mod[item[0]]):item[1] for item in output_list[0]}
            freq_dict = {str(llm_name):dict(Counter(sample_answers[llm_name][i])) for llm_name in collect_llms}
            weighted_freq_dict = {key: {subkey: value/ collect_conf[key]**0.5 for subkey, value in sublist.items()} for key, sublist in freq_dict.items()}
            
            merged = dict()
            for name, sublist in weighted_freq_dict.items():
                for key, values in sublist.items():
                    if key not in merged and key != "INVALID":
                        merged[key] = values
                    elif key != "INVALID":
                        merged[key] += values
            
            pred_llm_ans = max(merged, key=merged.get)
            
            
            selected_models.append(collect_llms)
            selected_models_len.append(len(collect_llms))
            total_lat = total_lat + sum([mod2lat[item] for item in collect_llms])
        
            if data_name == 'gsm8k':
                gold_llm_ans = float(gold_ans[i])
                pred_llm_ans = float(pred_llm_ans)
            elif data_name == 'mmlu':
                gold_llm_ans = gold_ans[i].strip()
                pred_llm_ans = pred_llm_ans.strip()

            if gold_llm_ans == pred_llm_ans:
                collect_acc += 1
                lab_list.append(1)
            else:
                lab_list.append(0)
        else:
            lab_list.append(0)
            
    return collect_acc/len(pred_list), total_lat/len(pred_list), selected_models, selected_models_len, lab_list
        

for i in range(len(llms)):
    print("*"*100)
    print(f"====== SelectLLM with {i+1} LLMS ======")
    print("*"*100)
    maj, maj_lat, selectllm, selectllm_len, lab_list_ = selectLLM(pred, conf, i+1)
    
    print("Accuracy with Maj(%): ", maj*100)
    print("Latency with Maj(Sec/Prompt) : ", maj_lat)
    
    print("*********** SelectLLM Model Distribution ****************")
    flat_selectllm = [item for sublist in selectllm for item in sublist]
    percentage_selectllm = {key: (value / len(flat_selectllm)) * 100 for key, value in Counter(flat_selectllm).items()}
    print(percentage_selectllm)

    print("*********** SelectLLM Model Length Distribution ****************")
    percentage_distribution = {key: (value / len(selectllm_len)) * 100 for key, value in Counter(selectllm_len).items()}
    print(percentage_distribution)
    Global_List.append([f' Policy3: SelectLLM with {i+1} LLMS', "--", maj*100, maj_lat])

    if (i+1) == 2:
        data_test["policy3"] = selectllm
        data_test["policy3_lab"] = lab_list_
        data_test.head()

In [26]:
data_test.head()

question  \
14327  The cyclic subgroup of Z_24 generated by 18 ha...   
14328  Find the order of the factor group Z_6/<3>. (A...   
14329  Statement 1 | A permutation that is a product ...   
14330  Find the order of the factor group (Z_4 x Z_12...   
14331  Find the maximum possible order for some eleme...   

                                              true_label  \
14327  ['maj_gemma-7b-it_CHAT', 'maj_gemma-7b_LM', 'm...   
14328     ['maj_gemma-7b-it_CHAT', 'maj_metamath-7b_LM']   
14329  ['maj_gemma-7b-it_CHAT', 'maj_gemma-7b_LM', 'm...   
14330                           ['maj_mistral-7b-lm_LM']   
14331  ['maj_gemma-7b_LM', 'maj_llama2-13b-chat_CHAT'...   

                                        prediction                  Oracle  \
14327  ['maj_gemma-7b_LM', 'maj_mistral-7b-lm_LM']  [maj_gemma-7b-it_CHAT]   
14328  ['maj_gemma-7b_LM', 'maj_mistral-7b-lm_LM']  [maj_gemma-7b-it_CHAT]   
14329  ['maj_gemma-7b_LM', 'maj_mistral-7b-lm_LM']  [maj_gemma-7b-it_CHAT]   
14330  ['maj_gemma-7b_LM', 'maj_mistral-7b-lm_LM']  [maj_mistral-7b-lm_LM]   
14331  ['maj_gemma-7b_LM', 'maj_mistral-7b-lm_LM']       [maj_gemma-7b_LM]   

       Oracle_lab                                               tops  \
14327           1  [maj_gemma-7b_LM, maj_mistral-7b-lm_LM, maj_mi...   
14328           1  [maj_gemma-7b_LM, maj_mistral-7b-lm_LM, maj_mi...   
14329           1  [maj_gemma-7b_LM, maj_mistral-7b-lm_LM, maj_mi...   
14330           1  [maj_gemma-7b_LM, maj_mistral-7b-lm_LM, maj_mi...   
14331           1  [maj_gemma-7b_LM, maj_mistral-7b-lm_LM, maj_mi...   

       tops_lab                                  policy1  policy1_lab  \
14327         1  [maj_gemma-7b_LM, maj_mistral-7b-lm_LM]            1   
14328         0  [maj_gemma-7b_LM, maj_mistral-7b-lm_LM]            0   
14329         1  [maj_gemma-7b_LM, maj_mistral-7b-lm_LM]            1   
14330         0  [maj_gemma-7b_LM, maj_mistral-7b-lm_LM]            1   
14331         1  [maj_gemma-7b_LM, maj_mistral-7b-lm_LM]            1   

                                       policy2  policy2_lab  \
14327  [maj_gemma-7b_LM, maj_mistral-7b-lm_LM]            1   
14328  [maj_gemma-7b_LM, maj_mistral-7b-lm_LM]            0   
14329  [maj_gemma-7b_LM, maj_mistral-7b-lm_LM]            1   
14330  [maj_gemma-7b_LM, maj_mistral-7b-lm_LM]            1   
14331  [maj_gemma-7b_LM, maj_mistral-7b-lm_LM]            1   

                                       policy3  policy3_lab  
14327  [maj_gemma-7b_LM, maj_mistral-7b-lm_LM]            1  
14328  [maj_gemma-7b_LM, maj_mistral-7b-lm_LM]            0  
14329  [maj_gemma-7b_LM, maj_mistral-7b-lm_LM]            1  
14330  [maj_gemma-7b_LM, maj_mistral-7b-lm_LM]            1  
14331  [maj_gemma-7b_LM, maj_mistral-7b-lm_LM]            1

In [ ]:
data_test.to_csv('mmlu_all_models_labels.csv', index=False)
data_test.to_csv('gsm8k_all_models_labels.csv', index=False)

In [28]:
global_df = pd.DataFrame(Global_List, columns=["Model", "Accuracy (%)", "Accuracy@maj(%)", "Latency (Sec/prompt)"])
global_df

Model  \
0                       Considered LLMs   
1                      Considered #LLMs   
2                Classifier-f1-weighted   
3                        Overall Oracle   
4                        Overall Oracle   
5                [maj_gemma-7b-it_CHAT]   
6                     [maj_gemma-7b_LM]   
7            [maj_llama2-13b-chat_CHAT]   
8                 [maj_llama2-7b-lm_LM]   
9                  [maj_metamath-7b_LM]   
10           [maj_mistral-7b-inst_CHAT]   
11               [maj_mistral-7b-lm_LM]   
12             Oracle with top-1 models   
13             Oracle with top-2 models   
14             Oracle with top-3 models   
15             Oracle with top-4 models   
16             Oracle with top-5 models   
17             Oracle with top-6 models   
18             Oracle with top-7 models   
19          Performance with top 1 LLMs   
20          Performance with top 2 LLMs   
21          Performance with top 3 LLMs   
22          Performance with top 4 LLMs   
23          Performance with top 5 LLMs   
24          Performance with top 6 LLMs   
25          Performance with top 7 LLMs   
26        Prformance with Bottom 1 LLMs   
27        Prformance with Bottom 2 LLMs   
28        Prformance with Bottom 3 LLMs   
29        Prformance with Bottom 4 LLMs   
30        Prformance with Bottom 5 LLMs   
31        Prformance with Bottom 6 LLMs   
32        Prformance with Bottom 7 LLMs   
33               Random baseline models   
34  Policy-1: Uppercound (Classifier) :   
35       Policy1: SelectLLM with 1 LLMS   
36       Policy1: SelectLLM with 2 LLMS   
37       Policy1: SelectLLM with 3 LLMS   
38       Policy1: SelectLLM with 4 LLMS   
39       Policy1: SelectLLM with 5 LLMS   
40       Policy1: SelectLLM with 6 LLMS   
41       Policy1: SelectLLM with 7 LLMS   
42  Policy-2: Uppercound (Classifier) :   
43       Policy2: SelectLLM with 1 LLMS   
44       Policy2: SelectLLM with 2 LLMS   
45       Policy2: SelectLLM with 3 LLMS   
46       Policy2: SelectLLM with 4 LLMS   
47       Policy2: SelectLLM with 5 LLMS   
48       Policy2: SelectLLM with 6 LLMS   
49       Policy2: SelectLLM with 7 LLMS   
50  Policy-3: Uppercound (Classifier) :   
51       Policy3: SelectLLM with 1 LLMS   
52       Policy3: SelectLLM with 2 LLMS   
53       Policy3: SelectLLM with 3 LLMS   
54       Policy3: SelectLLM with 4 LLMS   
55       Policy3: SelectLLM with 5 LLMS   
56       Policy3: SelectLLM with 6 LLMS   
57       Policy3: SelectLLM with 7 LLMS   

                                         Accuracy (%)  \
0   [maj_gemma-7b-it_CHAT, maj_gemma-7b_LM, maj_ll...   
1                                                   7   
2                                            0.682415   
3                                                  --   
4                                                  --   
5                                                  --   
6                                                  --   
7                                                  --   
8                                                  --   
9                                                  --   
10                                                 --   
11                                                 --   
12                                                 --   
13                                                 --   
14                                                 --   
15                                                 --   
16                                                 --   
17                                                 --   
18                                                 --   
19                                                 --   
20                                                 --   
21                                                 --   
22                                                 --   
23                                                 --   
24                                                 --   
25            

In [29]:
global_df.to_csv(path+'results.csv', index=False)